In [1]:
import os
import pickle
import pandas as pd
from pickle import Pickler
import git
import subprocess
from os import getcwd
from os import chdir
from subprocess import Popen
from subprocess import PIPE, STDOUT
import shutil
import xml.etree.ElementTree as ET
import json
import tqdm.auto as tqdm

In [2]:
dicts_cpp = os.listdir('dicts_cpp')
len(dicts_cpp)

80

In [3]:
i = 78 #CHANGE IT FOR EVERY FILE

In [4]:
file_name = dicts_cpp[i].split('.')[0]
repo_name = file_name.replace('_','/')
repo_name

'xbmc/xbmc'

In [5]:
try:
    with open('dicts_cpp/'+dicts_cpp[i], 'rb') as f:
        file_content = pickle.load(f)
except MemoryError:
    print("File cannot be opened")

In [6]:
file_content_df = pd.DataFrame.from_dict(file_content, orient='index')
hash_releases = file_content_df['release']
len(hash_releases)

30

In [7]:
folder = repo_name.split('/')[-1]
repo = git.Repo.clone_from('https://github.com/'+repo_name+'.git', folder)#no_checkout=True)

In [8]:
hash_and_dates = dict()

In [9]:
ROOT_PATH = getcwd()

git.Repo(ROOT_PATH+'/'+folder)

# Change to directory
chdir(ROOT_PATH+'/'+folder)

for release in hash_releases:
    with Popen(
        args=['git', 'show', '-s', '--format=%ci' , release],
        shell=False,
        stdout=PIPE,
        bufsize=1,
        universal_newlines=True,
    ) as process:

        for line in process.stdout:
            hash_and_dates[release] = line.strip()

In [10]:
chdir(ROOT_PATH)

In [11]:
getcwd()

'C:\\Users\\admin\\Downloads'

In [12]:
oldest_release = sorted(hash_and_dates.values())[0]
oldest_release

'2012-08-31 22:34:41 -0700'

In [13]:
commit_for_checkout = list(hash_and_dates.keys())[list(hash_and_dates.values()).index(oldest_release)]
commit_for_checkout

'12840c28d8fbfd71c26be798ff6b13828b05b168'

In [14]:
repo.git.checkout(commit_for_checkout)

''

In [15]:
for dirpath, subdirs, files_walk in os.walk(folder):
    for file_walk in files_walk:
        if file_walk.endswith('.cc'):
            without_ext = file_walk.split('.')[0]
            shutil.move(os.path.join(dirpath, file_walk), os.path.join(dirpath, without_ext+".cpp"))

In [16]:
print("Execute nicad for each file for release "+commit_for_checkout)

p = Popen(['C:/cygwin64/bin/bash.exe', '-c', '. /etc/profile; '+
'nicad6cross functions cpp C:/Users/Admin/Downloads/to_check '+ 
           'C:/Users/Admin/Downloads/'+folder], 
  stdout=PIPE, stderr=STDOUT)
p.communicate()[0]

Execute nicad for each file for release 12840c28d8fbfd71c26be798ff6b13828b05b168


b'\nNiCad Cross-Clone Detector v6.2 (13.11.20)\n\nconfig=C:/cygwin64/usr/local/lib/nicad/config/default.cfg\nsystem1=C:/Users/Admin/Downloads/to_check\nsystem2=C:/Users/Admin/Downloads/xbmc\nthreshold=0.30\ngranularity=functions\nlanguage=cpp\ntransform=none\nrename=blind\nfilter=none\nabstract=none\nnormalize=none\ncluster=yes\nreport=yes\ninclude=\nexclude=\n\nmer 25 gen 2023 14:20:19\n\nUsing previously extracted functions from cpp files in C:/Users/Admin/Downloads/to_check\n\nExtracted 69442 functions\n\nmer 25 gen 2023 14:20:20\n\nUsing previously extracted functions from cpp files in C:/Users/Admin/Downloads/xbmc\n\nExtracted 10988 functions\n\nUsing previously blind renamed extracted functions from cpp files in C:/Users/Admin/Downloads/to_check\n\nUsing previously blind renamed extracted functions from cpp files in C:/Users/Admin/Downloads/xbmc\n\nFinding cross-clones between 3 and 2500 lines at UPI threshold 0.30\n\nreal\t0m5,169s\nuser\t0m4,107s\nsys\t0m0,214s\n\nFound 1043 cl

In [17]:
idx = 0
files_to_check_with_cppcheck = dict()

if os.path.exists('to_check_functions-blind-crossclones/to_check_functions-blind-crossclones-0.30.xml'):
    tree = ET.parse('to_check_functions-blind-crossclones/to_check_functions-blind-crossclones-0.30.xml')
    root = tree.getroot()
    for clones in root.findall('clone'):
        for source in clones:
            if folder in source.attrib['file']:
                try:
                    files_to_check_with_cppcheck[idx] = {
                        'file': source.attrib['file'],
                        'start': source.attrib['startline'],
                        'end': source.attrib['endline']
                    }
                    idx = idx + 1
                except KeyError as e:
                    print(e)

'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'
'endline'


In [18]:
len(files_to_check_with_cppcheck.keys())

1011

In [ ]:
chdir(ROOT_PATH) # IF THERE ARE FILES .CC
for dirpath, subdirs, files_walk in os.walk(folder):
    for file_walk in files_walk:
        if file_walk.endswith('.cpp'):
            without_ext = file_walk.split('.')[0]
            shutil.move(os.path.join(dirpath, file_walk), os.path.join(dirpath, without_ext+".cc"))

In [19]:
chdir(ROOT_PATH+'/'+folder)

In [20]:
getcwd()

'C:\\Users\\admin\\Downloads\\xbmc'

In [21]:
clone_snippets_with_vuln = dict()
idx = 0

key_n = 0
for key in files_to_check_with_cppcheck.keys():
    try:
        print("Key "+str(key_n))
        code_context = []
        path = files_to_check_with_cppcheck[key]['file']
        #path = files_to_check_with_cppcheck[key]['file'].split('.')[0]+'.cc'
        print(path)
        proc = subprocess.run(["cppcheck", "--enable=style", "--template={cwe};{file};{line};{severity};{code}", path], capture_output=True)

        print(proc.stdout)
        result = proc.stderr.decode('utf-8')

        if result:
            items = result.split('\r\n')
            items = list(filter(None, items))

            for x, y in zip(*[iter(items)] * 2):
                row = x + y
                row = row.split(';')
                print("Flaw found at line "+row[2])
                print("Clone start a line "+files_to_check_with_cppcheck[key]['start']+' and end at line '+files_to_check_with_cppcheck[key]['end'])
                if int(row[2])>=int(files_to_check_with_cppcheck[key]['start']) and int(row[2])<=int(files_to_check_with_cppcheck[key]['end']):
                    code_context = []
                    with open(path, 'rb') as f:
                        content = f.readlines()
                        start = int(files_to_check_with_cppcheck[key]['start']) - 1
                        end = int(files_to_check_with_cppcheck[key]['end']) - 1
                        for number in range(start, end+1):
                            code_context.append(content[number].decode('utf-8'))

                    #chdir(ROOT_PATH+'/'+folder)
                    with Popen(
                    args=['git', 'log', '--reverse', '--pretty=format:%H', '-L', 
                          files_to_check_with_cppcheck[key]['start']+','+files_to_check_with_cppcheck[key]['end']+":"+path],
                    shell=False,
                    stdout=PIPE,
                    bufsize=1,
                    universal_newlines=True,
                    ) as process:
                        for line in process.stdout:
                            #print("commit "+line.strip())
                            origin_commit = line.strip()
                            break;

                        with Popen(
                            args=['git', 'show', '-s', '--format=%ci' , origin_commit],
                            shell=False,
                            stdout=PIPE,
                            bufsize=1,
                            universal_newlines=True,
                        ) as process:

                            for line in process.stdout:
                                date = line.strip()

                    clone_snippets_with_vuln[idx]={'repo': repo_name, 'origin_commit': origin_commit, 'file': path, #path.split(folder)[1][1:], 
                                                   'code_context': ''.join(code_context), 'commit_date': date, 'line_vuln': row[2], 'code_vuln': row[4]}
                    idx = idx + 1
                print()
            key_n = key_n + 1
    except UnicodeDecodeError:
        print("Error")

Key 0
C:/Users/Admin/Downloads/xbmc/xbmc/guilib/GUIListItem.cpp
b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIListItem.cpp ...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIListItem.cpp: HAS_DX...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIListItem.cpp: HAS_GL...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIListItem.cpp: HAS_GLES...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIListItem.cpp: _DEBUG...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIListItem.cpp: __GNUC__...\r\n'
Flaw found at line 101
Clone start a line 150 and end at line 173

Flaw found at line 112
Clone start a line 150 and end at line 173

Flaw found at line 116
Clone start a line 150 and end at line 173

Flaw found at line 116
Clone start a line 150 and end at line 173

Flaw found at line 116
Clone start a line 150 and end at line 173

Flaw found at line 41
Clone start a line 150 and end at line 173

Flaw f

b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\pictures\\Picture.cpp ...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\pictures\\Picture.cpp: LoadImage...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\pictures\\Picture.cpp: _LINUX...\r\n'
Flaw found at line 101
Clone start a line 50 and end at line 57

Key 6
C:/Users/Admin/Downloads/xbmc/xbmc/cores/dvdplayer/DVDPlayerSubtitle.cpp
b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\cores\\dvdplayer\\DVDPlayerSubtitle.cpp ...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\cores\\dvdplayer\\DVDPlayerSubtitle.cpp: DVDDEBUG_MESSAGE_TRACKER...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\cores\\dvdplayer\\DVDPlayerSubtitle.cpp: HAVE_CONFIG_H;WIN32...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\cores\\dvdplayer\\DVDPlayerSubtitle.cpp: HAVE_FFMPEG_AVCODEC_H;USE_EXTERNAL_FFMPEG;_LINUX...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\cores\\dvdplayer\\DVDPlayerSubtitle.cpp: HAVE_LIBAVCODEC_AVCODEC

b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIResizeControl.cpp ...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIResizeControl.cpp: HAS_DX...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIResizeControl.cpp: HAS_GL...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIResizeControl.cpp: HAS_GLES...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIResizeControl.cpp: TARGET_DARWIN_IOS...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIResizeControl.cpp: _DEBUG...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIResizeControl.cpp: _LINUX...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\guilib\\GUIResizeControl.cpp: __GNUC__...\r\n'
Flaw found at line 30
Clone start a line 241 and end at line 247

Flaw found at line 101
Clone start a line 241 and end at line 247

Flaw found at line 112
Clone start a line 241 and end at line 247

Flaw found at line 116
Clone start a line 24

b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\interfaces\\python\\xbmcmodule\\monitor.cpp ...\r\n'
Flaw found at line 31
Clone start a line 73 and end at line 77

Flaw found at line 37
Clone start a line 73 and end at line 77

Flaw found at line 42
Clone start a line 73 and end at line 77

Flaw found at line 49
Clone start a line 73 and end at line 77

Flaw found at line 63
Clone start a line 73 and end at line 77

Flaw found at line 150
Clone start a line 73 and end at line 77

Key 16
C:/Users/Admin/Downloads/xbmc/xbmc/interfaces/python/xbmcmodule/monitor.cpp
b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\interfaces\\python\\xbmcmodule\\monitor.cpp ...\r\n'
Flaw found at line 31
Clone start a line 85 and end at line 89

Flaw found at line 37
Clone start a line 85 and end at line 89

Flaw found at line 42
Clone start a line 85 and end at line 89

Flaw found at line 49
Clone start a line 85 and end at line 89

Flaw found at line 63
Clone start a line 85 and end at line 89

Fl

b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\interfaces\\python\\xbmcmodule\\player.cpp ...\r\n'
Flaw found at line 31
Clone start a line 288 and end at line 292

Flaw found at line 54
Clone start a line 288 and end at line 292

Flaw found at line 57
Clone start a line 288 and end at line 292

Flaw found at line 65
Clone start a line 288 and end at line 292

Flaw found at line 87
Clone start a line 288 and end at line 292

Flaw found at line 119
Clone start a line 288 and end at line 292

Flaw found at line 120
Clone start a line 288 and end at line 292

Flaw found at line 149
Clone start a line 288 and end at line 292

Flaw found at line 167
Clone start a line 288 and end at line 292

Flaw found at line 248
Clone start a line 288 and end at line 292

Flaw found at line 393
Clone start a line 288 and end at line 292

Flaw found at line 402
Clone start a line 288 and end at line 292

Flaw found at line 411
Clone start a line 288 and end at line 292

Flaw found at line 428
Clone s

...

b'Checking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp ...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: BYTE_ORDER...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: GUI;RARDLL;SFX_MODULE;_WIN_32;_WIN_CE...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: INCLUDEGLOBAL...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: NOCRYPT;SHELL_EXT...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: RARDLL...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: SILENT...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: SILENT;__GNUC__...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: S_IFLNK;_UNIX...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: USE_RC...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\strlist.cpp: WIN

b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\video\\Teletext.cpp ...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\video\\Teletext.cpp: HAS_SDL...\r\n'
Flaw found at line 3986
Clone start a line 460 and end at line 462

Flaw found at line 3990
Clone start a line 460 and end at line 462

Flaw found at line 3994
Clone start a line 460 and end at line 462

Flaw found at line 499
Clone start a line 460 and end at line 462

Flaw found at line 523
Clone start a line 460 and end at line 462

Flaw found at line 681
Clone start a line 460 and end at line 462

Flaw found at line 1269
Clone start a line 460 and end at line 462

Flaw found at line 1754
Clone start a line 460 and end at line 462

Flaw found at line 1757
Clone start a line 460 and end at line 462

Flaw found at line 1888
Clone start a line 460 and end at line 462

Flaw found at line 1891
Clone start a line 460 and end at line 462

Flaw found at line 1893
Clone start a line 460 and end at line 462

Flaw found at line 27

b'Checking C:\\Users\\admin\\Downloads\\xbmc\\xbmc\\music\\karaoke\\karaokelyricstextustar.cpp ...\r\n'
Flaw found at line 105
Clone start a line 40 and end at line 42

Flaw found at line 105
Clone start a line 40 and end at line 42

Flaw found at line 36
Clone start a line 40 and end at line 42

Flaw found at line 34
Clone start a line 40 and end at line 42

Flaw found at line 44
Clone start a line 40 and end at line 42

Flaw found at line 47
Clone start a line 40 and end at line 42

Flaw found at line 50
Clone start a line 40 and end at line 42

Flaw found at line 51
Clone start a line 40 and end at line 42

Flaw found at line 65
Clone start a line 40 and end at line 42

Flaw found at line 70
Clone start a line 40 and end at line 42

Flaw found at line 74
Clone start a line 40 and end at line 42

Flaw found at line 39
Clone start a line 40 and end at line 42

Key 932
C:/Users/Admin/Downloads/xbmc/xbmc/music/karaoke/karaokelyricstextlrc.cpp
b'Checking C:\\Users\\admin\\Downloads\\xbmc


Flaw found at line 55
Clone start a line 53 and end at line 55

Flaw found at line 56
Clone start a line 53 and end at line 55

Flaw found at line 58
Clone start a line 53 and end at line 55

Flaw found at line 60
Clone start a line 53 and end at line 55

Flaw found at line 61
Clone start a line 53 and end at line 55

Flaw found at line 62
Clone start a line 53 and end at line 55

Flaw found at line 63
Clone start a line 53 and end at line 55

Flaw found at line 64
Clone start a line 53 and end at line 55

Flaw found at line 66
Clone start a line 53 and end at line 55

Flaw found at line 67
Clone start a line 53 and end at line 55

Flaw found at line 82
Clone start a line 53 and end at line 55

Flaw found at line 84
Clone start a line 53 and end at line 55

Flaw found at line 41
Clone start a line 53 and end at line 55

Flaw found at line 43
Clone start a line 53 and end at line 55

Flaw found at line 45
Clone start a line 53 and end at line 55

Flaw found at line 46
Clone start a lin

b'Checking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp ...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: BELOW_NORMAL_PRIORITY_CLASS;_WIN_32;SFX_MODULE;_WIN_CE...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: BYTE_ORDER...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: GUI;RARDLL;SFX_MODULE;_WIN_32;_WIN_CE...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: INCLUDEGLOBAL...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: NOCRYPT;SHELL_EXT...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: RARDLL...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: SFX_MODULE;_WIN_CE...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: SFX_MODULE;_WIN_CE;_WIN_32...\r\nChecking C:\\Users\\admin\\Downloads\\xbmc\\lib\\UnrarXLib\\system.cpp: SILENT...\r\nChecking C:\\Users\\ad

In [22]:
prefix = getcwd()
prefix = prefix.replace('\\', '/')
print(prefix)
for key in clone_snippets_with_vuln.keys():
    print(clone_snippets_with_vuln[key]['file'])
    clone_snippets_with_vuln[key]['file'] = clone_snippets_with_vuln[key]['file'].replace('C:/Users/Admin/Downloads/'+folder+'/', '')
    print(clone_snippets_with_vuln[key]['file'])

C:/Users/admin/Downloads/xbmc
C:/Users/Admin/Downloads/xbmc/xbmc/utils/Splash.cpp
xbmc/utils/Splash.cpp
C:/Users/Admin/Downloads/xbmc/xbmc/cores/paplayer/AudioDecoder.cpp
xbmc/cores/paplayer/AudioDecoder.cpp
C:/Users/Admin/Downloads/xbmc/xbmc/cores/paplayer/AudioDecoder.cpp
xbmc/cores/paplayer/AudioDecoder.cpp
C:/Users/Admin/Downloads/xbmc/xbmc/cores/paplayer/AudioDecoder.cpp
xbmc/cores/paplayer/AudioDecoder.cpp
C:/Users/Admin/Downloads/xbmc/lib/cximage-6.0/CxImage/ximath.cpp
lib/cximage-6.0/CxImage/ximath.cpp
C:/Users/Admin/Downloads/xbmc/lib/cximage-6.0/CxImage/ximath.cpp
lib/cximage-6.0/CxImage/ximath.cpp
C:/Users/Admin/Downloads/xbmc/lib/cximage-6.0/CxImage/ximath.cpp
lib/cximage-6.0/CxImage/ximath.cpp
C:/Users/Admin/Downloads/xbmc/lib/cximage-6.0/CxImage/ximath.cpp
lib/cximage-6.0/CxImage/ximath.cpp
C:/Users/Admin/Downloads/xbmc/lib/cximage-6.0/CxImage/ximath.cpp
lib/cximage-6.0/CxImage/ximath.cpp
C:/Users/Admin/Downloads/xbmc/lib/cximage-6.0/CxImage/ximath.cpp
lib/cximage-6.0/CxI

In [23]:
 chdir(ROOT_PATH)

In [24]:
getcwd()

'C:\\Users\\admin\\Downloads'

In [25]:
if clone_snippets_with_vuln:
    clone_snippets_with_vuln_df = pd.DataFrame.from_dict(clone_snippets_with_vuln, orient='index')
else:
    print("Check next repository")
    shutil.rmtree('to_check_functions-blind-crossclones')
    all_files = os.listdir()

    for item in all_files:
        if item.endswith(".log"):
            os.remove(item)

    for item in all_files:
        if item.startswith(folder) and item.endswith('.xml'):
            os.remove(item)
    os.system('rmdir /S /Q "{}"'.format(folder))

In [26]:
clone_snippets_with_vuln_df = clone_snippets_with_vuln_df.drop_duplicates().reset_index(drop=True)
clone_snippets_with_vuln_df

repo                             origin_commit  \
0    xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   
1    xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   
2    xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   
3    xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   
4    xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   
..         ...                                       ...   
199  xbmc/xbmc  f8041eb08e25661cda1f35170004297e5c8430a3   
200  xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   
201  xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   
202  xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   
203  xbmc/xbmc  45285e8a9300cd754a760560640b75b09f98035e   

                                     file  \
0                   xbmc/utils/Splash.cpp   
1    xbmc/cores/paplayer/AudioDecoder.cpp   
2    xbmc/cores/paplayer/AudioDecoder.cpp   
3      lib/cximage-6.0/CxImage/ximath.cpp   
4      lib/cximage-6.0/CxImage/ximath.cpp   
..                                    ...   
199           xbmc/filesystem/APKFile.cpp   
200             lib/UnrarXLib/strlist.cpp   
201             lib/UnrarXLib/strlist.cpp   
202     xbmc/guilib/GUIListItemLayout.cpp   
203     xbmc/guilib/GUIListItemLayout.cpp   

                                          code_context  \
0    CSplash::CSplash(const CStdString& imageName) ...   
1    CAudioDecoder::CAudioDecoder()\r\n{\r\n  m_cod...   
2    CAudioDecoder::CAudioDecoder()\r\n{\r\n  m_cod...   
3    CxPoint2::CxPoint2(float const x_, float const...   
4    CxPoint2::CxPoint2(float const x_, float const...   
..                                                 ...   
199                CAPKFile::~CAPKFile()\r\n{\r\n}\r\n   
200            StringList::~StringList()\r\n{\r\n}\r\n   
201            StringList::~StringList()\r\n{\r\n}\r\n   
202  CGUIListItemLayout::~CGUIListItemLayout()\r\n{...   
203  CGUIListItemLayout::~CGUIListItemLayout()\r\n{...   

                   commit_date line_vuln  \
0    2009-09-23 01:49:50 +0000        36   
1    2009-09-23 01:49:50 +0000        37   
2    2009-09-23 01:49:50 +0000        31   
3    2009-09-23 01:49:50 +0000        15   
4    2009-09-23 01:49:50 +0000        16   
..                         ...       ...   
199  2012-08-08 18:59:21 -0400        46   
200  2009-09-23 01:49:50 +0000         9   
201  2009-09-23 01:49:50 +0000        11   
202  2009-09-23 01:49:50 +0000        53   
203  2009-09-23 01:49:50 +0000        55   

                                             code_vuln  
0                              m_ImageName = imageName  
1                                          ICodec()  ^  
2       CAudioDecoder::CAudioDecoder()               ^  
3                          CxIOFile(FILE* fp = NULL) ^  
4                                 virtual bool Close()  
..                                                 ...  
199                         virtual int GetChunkSize()  
200                             CryptKeyCacheItem()  ^  
201                        SaveFilePos(File &SaveFile)  
202                      virtual bool CanFocus() const  
203    virtual EVENT_RESULT SendMouseEvent(const CP...  

[204 rows x 7 columns]

In [113]:
ghCodeSnippetHistory = pd.DataFrame()

In [28]:
os.system('rmdir /S /Q "{}"'.format(folder))
repo = git.Repo.clone_from('https://github.com/'+repo_name+'.git', folder)

In [29]:
chdir(ROOT_PATH+'/'+folder)
getcwd()

'C:\\Users\\admin\\Downloads\\xbmc'

In [84]:
proc = subprocess.run(["git",  
                   "log",
                   '-M',
                   '--diff-filter=R',
                   "--summary",
                   "--reverse",
                      '>',
                      'file_renamed.txt'],
                  shell=True) # if at the latest commit the path does not exist

In [96]:
 # if at the latest commit the path does not exist
index_row = 0
with open('file_renamed.txt', 'r') as f:
    print(clone_snippets_with_vuln_df['file'][index_row].split('/')[-1])
    lines = f.readlines()
    replaced = False
    for line in lines:      
            if clone_snippets_with_vuln_df['file'][index_row].split('/')[-1] in line:
                print(line)
                sx_bracket = line.index('{')
                dx_bracket = line.index('}')
                index_arrow = line.index('=>')

                print("Old")
                old = line[sx_bracket+1:index_arrow-1]
                print(old.strip())
                print("To substitute")
                substitute = line[index_arrow+3:dx_bracket]
                print(substitute.strip())
                old_path = clone_snippets_with_vuln_df['file'][index_row]
                clone_snippets_with_vuln_df['file'][index_row] = clone_snippets_with_vuln_df['file'][index_row].replace(old.strip(), substitute.strip())
                replaced=True
                print(clone_snippets_with_vuln_df['file'][index_row].split('/')[-1])
if replaced == False:
    print("The file may be deleted")
else:
    print("The file path is renamed")

Splash.cpp
 rename {xbmc => src}/utils/Splash.cpp (100%)

Old
xbmc
To substitute
src
Splash.cpp
The file path is renamed


In [ ]:
for index in range(clone_snippets_with_vuln_df.shape[0]):
    print('Key_index '+str(index))
    print(clone_snippets_with_vuln_df['file'][index])
    repo.git.checkout('master')
    proc = subprocess.run(["git", 
                           "log",
                           '--pretty=format:%H',
                           "--follow",
                           "--",
                           clone_snippets_with_vuln_df['file'][index]], 
                          capture_output=True) 

    commits = proc.stdout.decode('utf-8').split('\n')
    commits.reverse()

        
    start_from = commits.index(clone_snippets_with_vuln_df['origin_commit'][index])+1

    print("Start from "+str(start_from))
    
    if len(commits)==1:
        print("This is the only commit on this file")
    else:
        try:
            for number in range(start_from, len(commits)):
                repo.git.checkout(commits[number])
                print('Checkout at commit '+commits[number])
                to_delete = []
                add_to_code_context = []
                
                print(commits[number])
                print("Run diff for "+clone_snippets_with_vuln_df['file'][index])
                proc = subprocess.run(["git", 
                                       "diff",
                                       commits[number-1]+".."+commits[number],
                                       '--',
                                        clone_snippets_with_vuln_df['file'][index]
                                      ],
                                      capture_output=True)

                if proc.stdout:
                    deleted = []
                    added = []
                    print("Diff for "+clone_snippets_with_vuln_df['file'][index])
                    with open('diff.txt', 'w', encoding='utf-8') as f:
                        f.write(proc.stdout.decode('utf-8'))
                    with open('diff.txt', 'r') as f:
                        context_index = None
                        context_line = None
                        print("Read diff")
                        content = f.readlines()

                        for line in content:
                            if line.startswith('-'):
                                deleted.append(line[1:])
                            if line.startswith('+'):
                                added.append(line[1:])

                        print("Analyze lines added")
                        print(added)
                        for added_line in added:
                            added_line_index = None
                            
                            if not added_line.startswith('++'):
                                print("Check "+added_line)
                
                                with open(clone_snippets_with_vuln_df['file'][index], 'r') as f:
                                    lines_cc = f.readlines();


                                    for x in lines_cc:
                                        x = x.replace('\n', '').replace('\r', '')
                                        if x != '' and x in clone_snippets_with_vuln_df['code_context'][index].split('\r\n')[0]:
                                            context_line = x
                                            print(x)
                                            print(clone_snippets_with_vuln_df['code_context'][index])
                                            print('###')
                                            break;

                                    print(context_index)
                                    print(added_line)
                                    if context_line:
                                        context_index = lines_cc.index(context_line+'\n')
                                        added_line_index = lines_cc.index(added_line)

                                        print(context_index)
                                        print(added_line_index)
                                        row_diff = context_index - added_line_index
                                        row_diff = abs(row_diff)
                                        print(row_diff)
                                        if row_diff>=0 and row_diff<=3:
                                            print("Add to code context")
                                            add_to_code_context.append(added_line)

                        print("Analyze lines deleted")
                        for line_deleted in deleted:
                            line_deleted = line_deleted.replace('\n', '')
                            if line_deleted:
                                if line_deleted  in clone_snippets_with_vuln_df['code_context'][index]:
                                    if line_deleted and line_deleted != '{' and line_deleted != '}':
                                        print("Append row")

                                        to_delete.append(line_deleted)



                to_change =  clone_snippets_with_vuln_df['code_context'][index]
                print("Code context updated before")
                print(to_change)
                if to_delete:
                    for entry in to_delete:
                        to_change = to_change.replace(entry, "")

                    print(commits[number])
                    print(to_delete)
                     #se sono rmaste solo parentesi graffe allora vedi se il file  stato spostato

                    #analyze_moves = False
                    for line in to_change:
                        if line == '\r' or line == '\n' or line == '{' or line=='}':
                            to_change = to_change.replace(line, '')
                if add_to_code_context:
                    string_to_add = ' '.join(add_to_code_context)
                    to_change = string_to_add + to_change

                print("Code context updated after")
                print(to_change)

                if to_change == '':
                    print('Check moves for '+clone_snippets_with_vuln_df['file'][index][1:])
                
                with Popen(
                    args=['git', 'show', '-s', '--format=%ci' ,  commits[number]],
                    shell=False,
                    stdout=PIPE,
                    bufsize=1,
                    universal_newlines=True,
                ) as process:

                    for line in process.stdout:
                        date = line.strip()
                ghCodeSnippetHistory = ghCodeSnippetHistory.append({'repo': repo_name, 'origin_commit': commits[number], 
                                                    'file': clone_snippets_with_vuln_df['file'][index], 
                                           'code_context': to_change, 
                                                    'commit_date': date}, ignore_index=True)
                print()
            
        except UnicodeDecodeError:
            print("Encoding error")

Key_index 0
xbmc/utils/Splash.cpp
Start from 1
Checkout at commit 8993f0f3a3e2805b5b8728e62c6c1c072b47cbbc
8993f0f3a3e2805b5b8728e62c6c1c072b47cbbc
Run diff for xbmc/utils/Splash.cpp
Diff for xbmc/utils/Splash.cpp
Read diff
Analyze lines added
['++ b/xbmc/utils/Splash.cpp\n']
Analyze lines deleted
Code context updated before
CSplash::CSplash(const CStdString& imageName) : CThread("CSplash")
{
  m_ImageName = imageName;
  fade = 0.5;
  m_messageLayout = NULL;
  m_image = NULL;
  m_layoutWasLoading = false;
}

Code context updated after
CSplash::CSplash(const CStdString& imageName) : CThread("CSplash")
{
  m_ImageName = imageName;
  fade = 0.5;
  m_messageLayout = NULL;
  m_image = NULL;
  m_layoutWasLoading = false;
}




C:\Users\admin\AppData\Local\Temp\ipykernel_167372\2000226195.py:142: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ghCodeSnippetHistory = ghCodeSnippetHistory.append({'repo': repo_name, 'origin_commit': commits[number],


Checkout at commit c51b1189e3d5353e842991f5859ddcea0f73e426
c51b1189e3d5353e842991f5859ddcea0f73e426
Run diff for xbmc/utils/Splash.cpp
Diff for xbmc/utils/Splash.cpp
Read diff
Analyze lines added
['++ b/xbmc/utils/Splash.cpp\n', '#include "guilib/GUIImage.h"\n', '#include "filesystem/File.h"\n', '#include "windowing/WindowingFactory.h"\n', '#include "rendering/RenderSystem.h"\n']
Check #include "guilib/GUIImage.h"

CSplash::CSplash(const CStdString& imageName)
CSplash::CSplash(const CStdString& imageName) : CThread("CSplash")
{
  m_ImageName = imageName;
  fade = 0.5;
  m_messageLayout = NULL;
  m_image = NULL;
  m_layoutWasLoading = false;
}

###
None
#include "guilib/GUIImage.h"

31
23
8
Check #include "filesystem/File.h"

CSplash::CSplash(const CStdString& imageName)
CSplash::CSplash(const CStdString& imageName) : CThread("CSplash")
{
  m_ImageName = imageName;
  fade = 0.5;
  m_messageLayout = NULL;
  m_image = NULL;
  m_layoutWasLoading = false;
}

###
31
#include "filesystem/Fil

C:\Users\admin\AppData\Local\Temp\ipykernel_167372\2000226195.py:142: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ghCodeSnippetHistory = ghCodeSnippetHistory.append({'repo': repo_name, 'origin_commit': commits[number],



Checkout at commit 7764bf6d7917fb2eee2b72133b3663817f404b65
7764bf6d7917fb2eee2b72133b3663817f404b65
Run diff for xbmc/utils/Splash.cpp
Diff for xbmc/utils/Splash.cpp
Read diff
Analyze lines added
['++ b/xbmc/utils/Splash.cpp\n', '  g_graphicsContext.SetRenderingResolution(RES_HDTV_720p, true);  \n', '  CGUIImage* image = new CGUIImage(0, 0, 0, 0, 1280, 720, m_ImageName);  \n', '  image->SetAspectRatio(CAspectRatio::AR_CENTER);  \n']
Check   g_graphicsContext.SetRenderingResolution(RES_HDTV_720p, true);  

CSplash::CSplash(const CStdString& imageName)
CSplash::CSplash(const CStdString& imageName) : CThread("CSplash")
{
  m_ImageName = imageName;
  fade = 0.5;
  m_messageLayout = NULL;
  m_image = NULL;
  m_layoutWasLoading = false;
}

###
None
  g_graphicsContext.SetRenderingResolution(RES_HDTV_720p, true);  

31
54
23
Check   CGUIImage* image = new CGUIImage(0, 0, 0, 0, 1280, 720, m_ImageName);  

CSplash::CSplash(const CStdString& imageName)
CSplash::CSplash(const CStdString& imageN

...

C:\Users\admin\AppData\Local\Temp\ipykernel_167372\2000226195.py:142: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ghCodeSnippetHistory = ghCodeSnippetHistory.append({'repo': repo_name, 'origin_commit': commits[number],


Checkout at commit c51b1189e3d5353e842991f5859ddcea0f73e426
c51b1189e3d5353e842991f5859ddcea0f73e426
Run diff for xbmc/GUIPassword.cpp
Diff for xbmc/GUIPassword.cpp
Read diff
Analyze lines added
['++ b/xbmc/GUIPassword.cpp\n', '#include "dialogs/GUIDialogGamepad.h"\n', '#include "dialogs/GUIDialogKeyboard.h"\n', '#include "dialogs/GUIDialogNumeric.h"\n', '#include "dialogs/GUIDialogOK.h"\n', '#include "settings/GUIDialogLockSettings.h"\n', '#include "settings/GUIDialogProfileSettings.h"\n', '#include "settings/Settings.h"\n', '#include "settings/GUISettings.h"\n', '#include "guilib/GUIWindowManager.h"\n', '#include "guilib/LocalizeStrings.h"\n']
Check #include "dialogs/GUIDialogGamepad.h"

CGUIPassword::CGUIPassword(void)
CGUIPassword::CGUIPassword(void)
{
  iMasterLockRetriesLeft = -1;
  bMasterUser = false;
}

###
None
#include "dialogs/GUIDialogGamepad.h"

39
24
15
Check #include "dialogs/GUIDialogKeyboard.h"

CGUIPassword::CGUIPassword(void)
CGUIPassword::CGUIPassword(void)
{
  iMa

C:\Users\admin\AppData\Local\Temp\ipykernel_167372\2000226195.py:142: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ghCodeSnippetHistory = ghCodeSnippetHistory.append({'repo': repo_name, 'origin_commit': commits[number],



Checkout at commit 82e11e958ec30b3ba216fea44f9b4c2beb5bbe75
82e11e958ec30b3ba216fea44f9b4c2beb5bbe75
Run diff for xbmc/GUIPassword.cpp
Diff for xbmc/GUIPassword.cpp
Read diff
Analyze lines added
['++ b/xbmc/GUIPassword.cpp\n']
Analyze lines deleted
Code context updated before
CGUIPassword::CGUIPassword(void)
{
  iMasterLockRetriesLeft = -1;
  bMasterUser = false;
}

Code context updated after
CGUIPassword::CGUIPassword(void)
{
  iMasterLockRetriesLeft = -1;
  bMasterUser = false;
}




C:\Users\admin\AppData\Local\Temp\ipykernel_167372\2000226195.py:142: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ghCodeSnippetHistory = ghCodeSnippetHistory.append({'repo': repo_name, 'origin_commit': commits[number],


In [ ]:
chdir(ROOT_PATH)
getcwd()

In [ ]:
ghCodeSnippetHistory

In [ ]:
rows_to_check_move = ghCodeSnippetHistory.loc[ghCodeSnippetHistory['code_context']=='']    

In [ ]:
rows_to_check_move

In [ ]:
chdir(ROOT_PATH+'/'+folder)

In [ ]:
#skip if rows_to_check_move is empty
proc = subprocess.run(["git", 
                   "log",
                   '-M',
                   '--diff-filter=R',
                   "--summary",
                   "--reverse",
                      '>',
                      'file_renamed.txt'],
                  shell=True) 

In [ ]:
# skip if rows_to_check_move is empty
files = list(pd.unique(rows_to_check_move['file']))
print(len(files))
for _, row in rows_to_check_move.iterrows():
    lines_collected = []
    start_from_this_commit = row['origin_commit']
    start_read = False 
    replaced = False

    with open('file_renamed.txt', 'r') as f:
        
        lines = f.readlines()
        show = False
        for line in lines:
            if line.strip().startswith('commit '+start_from_this_commit):
                show = True
            
            if line.strip().startswith('commit ') and not line.strip().startswith('commit '+start_from_this_commit):
                show = False
            if show:
                if row['file'].split('/')[-1] in line and row['file'] in files:
                    print(line)
                    start = line.index('{')+1
                    end = line.index('}')
                    between_brackets = line[start:end]
                    index_arrow = between_brackets.index('=>')
                    print(between_brackets)
                    print("Old")
                    old = between_brackets[0:index_arrow]
                    print(old.strip())
                    print("To substitute")
                    substitute = between_brackets[index_arrow+3:len(between_brackets)]
                    print(substitute.strip())
                    old_path = row['file']
                    files.remove(old_path)
                    row['file'] = row['file'].replace(old.strip(), substitute.strip())
                    replaced = True
                    print(row['file'])
                    
                    with Popen(
                            args=['git', 'show', '-s', '--format=%ci' ,  start_from_this_commit],
                            shell=False,
                            stdout=PIPE,
                            bufsize=1,
                            universal_newlines=True,
                        ) as process:

                            for line in process.stdout:
                                date = line.strip()
                    index_row =  clone_snippets_with_vuln_df.loc[clone_snippets_with_vuln_df['file']==old_path].index[0]
                    ghCodeSnippetHistory.loc[_] = {'repo': repo_name, 'origin_commit': start_from_this_commit, 
                                    'file': row['file'], 
                           'code_context': clone_snippets_with_vuln_df.iloc[index_row, 3]    , 
                                    'commit_date': date}
                    

    if replaced == False and row['file'] in files:
        print("The file may be deleted")
        ghCodeSnippetHistory = ghCodeSnippetHistory.drop([_])
    if replaced==True:
        print("The file path is renamed")

In [ ]:
chdir(ROOT_PATH)
getcwd()

In [ ]:
ghCodeSnippetHistory

In [ ]:
chdir(ROOT_PATH+'/'+folder)
getcwd()

In [ ]:
len(ghCodeSnippetHistory)

In [ ]:
ghCodeSnippetHistory

In [ ]:
ghCodeSnippetHistory_aftercppcheck = dict()
idx = 0
num = 0
for _, row in ghCodeSnippetHistory.iterrows():

    print(_)
    print(row['origin_commit'])
    print(row['file'])
    repo.git.checkout(row['origin_commit'])
    proc = subprocess.run(["cppcheck", "--enable=style", "--template={cwe};{file};{line};{severity};{code}", row['file']], capture_output=True)
    result = proc.stderr.decode('utf-8')
    print(proc.stdout)

    if proc.stdout.decode('utf-8') == 'cppcheck: error: could not find or open any of the paths given.\r\n':
        break;

    if result:
        items = result.split('\r\n')
        items = list(filter(None, items))
        for x, y in zip(*[iter(items)] * 2):
            row = x + y
            row = row.split(';')

            if not row[2]=='0':
                print("Flaw found at line "+row[2])
                ghCodeSnippetHistory_aftercppcheck[idx] = {
                    'repo': ghCodeSnippetHistory['repo'][_],
                    'origin_commit': ghCodeSnippetHistory['origin_commit'][_],
                    'file': ghCodeSnippetHistory['file'][_],
                    'code_context': ghCodeSnippetHistory['code_context'][_],
                    'commit_date': ghCodeSnippetHistory['commit_date'][_],
                    'line_vuln': row[2],
                    'code_vuln': row[4]
                }
                idx = idx + 1
            else:
                print("Syntax error")
                break;
    else:
        ghCodeSnippetHistory_aftercppcheck[idx] = {
            'repo': ghCodeSnippetHistory['repo'][_],
            'origin_commit': ghCodeSnippetHistory['origin_commit'][_] ,
            'file': ghCodeSnippetHistory['file'][_] ,
            'code_context': ghCodeSnippetHistory['code_context'][_], 
            'commit_date': ghCodeSnippetHistory['commit_date'][_],
            'line_vuln': '',
            'code_vuln': ''
        }
        idx = idx + 1
    num = num + 1
    print() 

In [ ]:
ghCodeSnippetHistory_aftercppcheck

In [ ]:
ghCodeSnippetHistory_aftercppcheck = pd.DataFrame.from_dict(ghCodeSnippetHistory_aftercppcheck, orient='index')

In [ ]:
ghCodeSnippetHistory_aftercppcheck = ghCodeSnippetHistory_aftercppcheck.reset_index(drop=True)

In [ ]:
len(ghCodeSnippetHistory_aftercppcheck)

In [ ]:
ghCodeSnippetHistory_aftercppcheck

In [ ]:
files = pd.unique(ghCodeSnippetHistory_aftercppcheck['file'])

for file in files:
    print(file)

In [ ]:
clone_snippets_with_vuln_df.loc[clone_snippets_with_vuln_df['file']==files[0]]

In [ ]:
ghCodeSnippetHistory_aftercppcheck.loc[ghCodeSnippetHistory_aftercppcheck['file']==files[0]]

In [ ]:
code_initial = pd.unique(clone_snippets_with_vuln_df['code_vuln'])
indexes = []
for code in code_initial:
    code = code.replace('\r', '').replace('\n','').replace('^','') 
    

    for _,row in ghCodeSnippetHistory_aftercppcheck.iterrows():
        code_gh = ghCodeSnippetHistory_aftercppcheck['code_vuln'][_]
        code_gh = code_gh.replace('\r', '').replace('\n','').replace('^','') 
        if code in code_gh:
            indexes.append(_)

In [ ]:
ghCodeSnippetHistory_aftercppcheck.iloc[indexes].drop_duplicates()# where code_vuln is equal

In [ ]:
ghCodeSnippetHistory_aftercppcheck

In [ ]:
chdir(ROOT_PATH)
ghCodeSnippetHistory_aftercppcheck.to_csv('GHCodeSnippetHistory/history_'+file_name+".csv")